In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import col, expr, substring, when, lit
from pyspark.sql.types import DoubleType, IntegerType

# Initialize SparkSession
spark = SparkSession.builder \
    .appName("NOAA Snow Data Processing") \
    .config("spark.hadoop.fs.s3a.connection.maximum", "200") \
    .config("spark.hadoop.fs.s3a.threads.max", "200") \
    .config("spark.hadoop.fs.s3a.multipart.size", "104857600") \
    .config("spark.hadoop.fs.s3a.fast.upload", "true") \
    .config("spark.speculation", "true") \
    .getOrCreate()

# Define S3 path
s3_path = "s3a://noaa-isd-pds/data/2025/"
#s3_path = "s3a://noaa-isd-pds/data/2025/010010-99999-2025.gz"

# Helper function for substring extraction
def extract_field(value_col, marker, offset, length):
    """
    Extracts a substring from the value column based on a marker, offset, and length.

    Args:
        value_col (str): The column name or expression to extract from.
        marker (str): The string marker to locate within the value.
        offset (int): The position offset from the marker.
        length (int): The length of the substring to extract.

    Returns:
        Column: A PySpark Column object with the extracted substring.
    """
    return expr(f"substring({value_col}, instr({value_col}, '{marker}') + {offset}, {length})")

# Read and process the data in a single pipeline
df = spark.read.text(s3_path).filter(
    col("value").rlike("AJ1|AK1|AL1|AL2|AL3|AL4|AM1|AN1")
).select(
    # Mandatory fields
    substring(col("value"), 5, 6).alias("weather_station_usaf_id"),
    substring(col("value"), 11, 5).alias("weather_station_wban_id"),
    substring(col("value"), 16, 8).alias("observation_date"),
    substring(col("value"), 24, 4).alias("observation_time"),
    (substring(col("value"), 29, 6).cast(DoubleType()) / 1000).alias("latitude_dec"),
    (substring(col("value"), 35, 7).cast(DoubleType()) / 1000).alias("longitude_dec"),
    substring(col("value"), 47, 5).cast(IntegerType()).alias("elevation"),

    # Snow-related fields
    when(col("value").contains("AJ1"), lit("AJ1"))
    .when(col("value").contains("AK1"), lit("AK1"))
    .when(col("value").contains("AL1"), lit("AL1"))
    .when(col("value").contains("AL2"), lit("AL2"))
    .when(col("value").contains("AL3"), lit("AL3"))
    .when(col("value").contains("AL4"), lit("AL4"))
    .when(col("value").contains("AM1"), lit("AM1"))
    .when(col("value").contains("AN1"), lit("AN1"))
    .alias("identifier"),

    # AJ1 Fields
    extract_field("value", "AJ1", 3, 4).alias("snow_depth"),
    extract_field("value", "AJ1", 7, 1).alias("snow_condition_code"),
    extract_field("value", "AJ1", 8, 1).alias("snow_quality_code"),
    extract_field("value", "AJ1", 9, 6).alias("equiv_water_depth"),
    extract_field("value", "AJ1", 15, 1).alias("equiv_water_condition_code"),
    extract_field("value", "AJ1", 16, 1).alias("equiv_water_quality_code"),

    # AK1 Fields
    extract_field("value", "AK1", 3, 4).alias("greatest_snow_depth"),
    extract_field("value", "AK1", 7, 1).alias("greatest_condition_code"),
    extract_field("value", "AK1", 8, 6).alias("greatest_dates_of_occurrence"),
    extract_field("value", "AK1", 14, 1).alias("greatest_quality_code"),

    # AL1 to AL4 Fields
    extract_field("value", "AL1", 3, 2).alias("al1_accumulation_period_quantity"),
    extract_field("value", "AL1", 5, 3).alias("al1_accumulation_depth"),
    extract_field("value", "AL1", 8, 1).alias("al1_accumulation_condition_code"),
    extract_field("value", "AL1", 9, 1).alias("al1_accumulation_quality_code"),
    extract_field("value", "AL2", 3, 2).alias("al2_accumulation_period_quantity"),
    extract_field("value", "AL2", 5, 3).alias("al2_accumulation_depth"),
    extract_field("value", "AL2", 8, 1).alias("al2_accumulation_condition_code"),
    extract_field("value", "AL2", 9, 1).alias("al2_accumulation_quality_code"),
    extract_field("value", "AL3", 3, 2).alias("al3_accumulation_period_quantity"),
    extract_field("value", "AL3", 5, 3).alias("al3_accumulation_depth"),
    extract_field("value", "AL3", 8, 1).alias("al3_accumulation_condition_code"),
    extract_field("value", "AL3", 9, 1).alias("al3_accumulation_quality_code"),
    extract_field("value", "AL4", 3, 2).alias("al4_accumulation_period_quantity"),
    extract_field("value", "AL4", 5, 3).alias("al4_accumulation_depth"),
    extract_field("value", "AL4", 8, 1).alias("al4_accumulation_condition_code"),
    extract_field("value", "AL4", 9, 1).alias("al4_accumulation_quality_code"),

    # AM1 Fields
    extract_field("value", "AM1", 3, 4).alias("greatest_accumulation_depth"),
    extract_field("value", "AM1", 7, 1).alias("am1_accumulation_condition_code"),
    extract_field("value", "AM1", 8, 4).alias("am1_dates_of_occurrence_1"),
    extract_field("value", "AM1", 12, 4).alias("am1_dates_of_occurrence_2"),
    extract_field("value", "AM1", 16, 4).alias("am1_dates_of_occurrence_3"),
    extract_field("value", "AM1", 20, 1).alias("am1_accumulation_quality_code"),

    # AN1 Fields
    extract_field("value", "AN1", 3, 3).alias("monthly_period_quantity"),
    extract_field("value", "AN1", 6, 4).alias("monthly_accumulation_depth"),
    extract_field("value", "AN1", 10, 1).alias("monthly_condition_code"),
    extract_field("value", "AN1", 11, 1).alias("monthly_quality_code")
).select(
    # Cast all fields to strings for consistency
    *(col(field).cast("string").alias(field) for field in [
        "weather_station_usaf_id", "weather_station_wban_id", "observation_date", "observation_time",
        "latitude_dec", "longitude_dec", "elevation", "identifier", "snow_depth", "snow_condition_code",
        "snow_quality_code", "equiv_water_depth", "equiv_water_condition_code", "equiv_water_quality_code",
        "greatest_snow_depth", "greatest_condition_code", "greatest_dates_of_occurrence", "greatest_quality_code",
        "al1_accumulation_period_quantity", "al1_accumulation_depth", "al1_accumulation_condition_code",
        "al1_accumulation_quality_code", "al2_accumulation_period_quantity", "al2_accumulation_depth",
        "al2_accumulation_condition_code", "al2_accumulation_quality_code", "al3_accumulation_period_quantity",
        "al3_accumulation_depth", "al3_accumulation_condition_code", "al3_accumulation_quality_code",
        "al4_accumulation_period_quantity", "al4_accumulation_depth", "al4_accumulation_condition_code",
        "al4_accumulation_quality_code", "greatest_accumulation_depth", "am1_accumulation_condition_code",
        "am1_dates_of_occurrence_1", "am1_dates_of_occurrence_2", "am1_dates_of_occurrence_3",
        "am1_accumulation_quality_code", "monthly_period_quantity", "monthly_accumulation_depth",
        "monthly_condition_code", "monthly_quality_code"
    ])
)

# Register the DataFrame as a temporary view in Spark
df.createOrReplaceTempView("df_temp")

# Create or replace a Delta table in the Databricks metastore
spark.sql("""
CREATE OR REPLACE TABLE df_delta
USING DELTA
AS SELECT * FROM df_temp
""")





Out[1]: DataFrame[num_affected_rows: bigint, num_inserted_rows: bigint]

In [0]:
# Optimize Delta table
spark.sql("OPTIMIZE df_delta ZORDER BY (observation_date, weather_station_usaf_id)")


# Confirm data in Delta table
spark.sql("SELECT * FROM df_delta LIMIT 10").show()

+-----------------------+-----------------------+----------------+----------------+------------+-------------+---------+----------+----------+-------------------+-----------------+-----------------+--------------------------+------------------------+-------------------+-----------------------+----------------------------+---------------------+--------------------------------+----------------------+-------------------------------+-----------------------------+--------------------------------+----------------------+-------------------------------+-----------------------------+--------------------------------+----------------------+-------------------------------+-----------------------------+--------------------------------+----------------------+-------------------------------+-----------------------------+---------------------------+-------------------------------+-------------------------+-------------------------+-------------------------+-----------------------------+---------------

In [0]:
%sql
select * from df_delta limit 10


weather_station_usaf_id weather_station_wban_id observation_date observation_time latitude_dec longitude_dec elevation identifier snow_depth snow_condition_code snow_quality_code equiv_water_depth equiv_water_condition_code equiv_water_quality_code greatest_snow_depth greatest_condition_code greatest_dates_of_occurrence greatest_quality_code al1_accumulation_period_quantity al1_accumulation_depth al1_accumulation_condition_code al1_accumulation_quality_code al2_accumulation_period_quantity al2_accumulation_depth al2_accumulation_condition_code al2_accumulation_quality_code al3_accumulation_period_quantity al3_accumulation_depth al3_accumulation_condition_code al3_accumulation_quality_code al4_accumulation_period_quantity al4_accumulation_depth al4_accumulation_condition_code al4_accumulation_quality_code greatest_accumulation_depth am1_accumulation_condition_code am1_dates_of_occurrence_1 am1_dates_of_occurrence_2 am1_dates_of_occurrence_3 am1_accumulation_quality_code monthly_period_quantity monthly_accumulation_depth monthly_condition_code monthly_quality_code 027870 99999 20250101 0000 63.083 24.267 171 AJ1 0017 3 1 001700 9 9 9502 7 870999 9 95 027 8 7 95 027 8 7 95 027 8 7 95 027 8 7 9502 7 8709 9999 2025 0 950 2787 0 9 027870 99999 20250101 0100 63.083 24.267 171 AJ1 0017 3 1 001700 9 9 9502 7 870999 9 95 027 8 7 95 027 8 7 95 027 8 7 95 027 8 7 9502 7 8709 9999 2025 0 950 2787 0 9 027870 99999 20250101 0200 63.083 24.267 171 AJ1 0017 3 1 001700 9 9 9502 7 870999 9 95 027 8 7 95 027 8 7 95 027 8 7 95 027 8 7 9502 7 8709 9999 2025 0 950 2787 0 9 027870 99999 20250101 0300 63.083 24.267 171 AJ1 0017 3 1 001700 9 9 9502 7 870999 9 95 027 8 7 95 027 8 7 95 027 8 7 95 027 8 7 9502 7 8709 9999 2025 0 950 2787 0 9 027870 99999 20250101 0400 63.083 24.267 171 AJ1 0017 3 1 001700 9 9 0102 7 870999 9 01 027 8 7 01 027 8 7 01 027 8 7 01 027 8 7 0102 7 8709 9999 2025 0 010 2787 0 9 027870 99999 20250101 0500 63.083 24.267 171 AJ1 0017 3 1 001700 9 9 9502 7 870999 9 95 027 8 7 95 027 8 7 95 027 8 7 95 027 8 7 9502 7 8709 9999 2025 0 950 2787 0 9 027870 99999 20250101 0600 63.083 24.267 171 AJ1 0017 3 1 001700 9 9 5602 7 870999 9 56 027 8 7 56 027 8 7 56 027 8 7 56 027 8 7 5602 7 8709 9999 2025 0 560 2787 0 9 027870 99999 20250101 0700 63.083 24.267 171 AJ1 0017 3 1 001700 9 9 0102 7 870999 9 01 027 8 7 01 027 8 7 01 027 8 7 01 027 8 7 0102 7 8709 9999 2025 0 010 2787 0 9 027870 99999 20250101 0800 63.083 24.267 171 AJ1 0017 3 1 001700 9 9 2302 7 870999 9 23 027 8 7 23 027 8 7 23 027 8 7 23 027 8 7 2302 7 8709 9999 2025 0 230 2787 0 9 027870 99999 20250101 0900 63.083 24.267 171 AJ1 0017 3 1 001700 9 9 0102 7 870999 9 01 027 8 7 01 027 8 7 01 027 8 7 01 027 8 7 0102 7 8709 9999 2025 0 010 2787 0 9

In [0]:
%sql
select distinct latitude_dec, longitude_dec
from df_delta


latitude_dec longitude_dec 49.217 4.15 73.217 -119.533 56.65 90.55 42.9 133.9 46.4 96.25 59.967 30.3 49.8 19.0 46.667 -60.4 44.633 -63.517 47.333 28.083 35.0 102.9 27.33 117.47 42.231 -83.331 35.457 133.066 42.933 -78.717 65.767 46.2 56.8 105.8 53.867 -0.433 72.017 -94.2 46.433 -63.833 62.567 11.383 48.15 -80.0 51.15 -80.39 37.5 -77.333 38.651 32.922 68.633 -95.85 47.425 13.634 51.1 -100.05 48.767 30.233 55.183 -6.167 46.433 9.767 41.7 15.95 52.0 70.95 32.5 80.08 46.531 -87.549 63.383 28.667 49.967 2.704 45.79 24.036 48.767 121.917 48.533 -58.55 48.65 19.15 56.883 35.867 51.4 51.95 30.05 101.97 35.167 126.9 44.117 21.95 48.517 -72.267 64.217 41.667 59.633 133.033 49.2 14.35 52.383 140.467 50.867 156.683 51.767 -104.2 51.867 -1.683 39.083 68.867 2.967 -75.283 42.517 72.217 33.58 102.97 63.233 29.233 63.841 27.221 44.833 -0.683 46.318 23.139 57.133 25.917 50.48 121.68 49.383 1.183 46.733 83.0 52.967 78.65 61.76 -121.238 57.417 67.083 54.333 89.283 50.0 14.45 45.5 64.083 47.82 -83.786 49.028 -119.498 52.417 136.5 54.317 48.333 50.217 66.833 52.819 -97.616 49.9 -99.35 45.369 -72.733 74.139 -119.992 47.943 -97.183 42.454 -2.321 41.183 41.817 68.083 27.183 63.833 27.217 44.25 28.267 49.433 127.35 47.167 119.933 63.267 33.417 62.483 86.283 49.667 12.683 49.033 21.317 49.8 92.083 57.917 22.05 60.363 6.281 51.083 -97.55 68.05 16.083 46.783 23.567 35.17 126.89 43.28 20.8 49.933 15.383 54.117 159.983 53.367 -107.55 68.317 -133.517 51.083 -3.6 49.667 31.0 48.304 -114.264 39.5 67.6 76.531 -68.703 45.717 4.933 63.733 25.7 47.344 22.094 66.033 117.4 52.417 16.85 59.3 4.867 43.0 -82.3 49.083 -116.5 38.1 69.317 46.817 8.417 40.533 44.383 37.35 46.167 46.169 22.726 54.417 34.017 62.233 74.483 51.35 112.467 57.65 136.15 53.183 48.4 39.044 -84.672 49.7 -88.317 49.35 -123.2 37.483 69.383 41.029 43.876 42.986 144.371 44.883 -93.229 33.565 -86.745 32.683 -4.733 66.567 25.817 44.883 22.417 43.783 87.617 52.05 92.167 58.617 125.367 56.1 74.633 46.237 15.231 57.65 99.533 54.95 41.767 43.508 16.426 48.85 111.45 48.833 -72.533 66.233 -128.65 3.55 -76.367 44.883 -93.217 47.5 9.75 31.42 121.45 44.915 4.972 35.883 128.65 45.183 22.05 37.567 126.967 58.088 93.157 65.833 65.933 47.967 -84.783 53.033 -0.5 50.117 14.533 61.733 102.817 44.65 -63.617 53.767 20.417 51.168 5.47 50.633 -97.05 -16.433 -151.75 51.25 51.283 -31.668 -63.882 47.367 26.933 35.567 129.317 48.767 18.6 42.747 -73.799 50.8 75.7 58.472 -78.077 74.717 -94.969 56.35 78.35 53.425 -112.678 63.767 121.617 62.533 111.233 60.656 7.276 46.77 -65.0 63.233 11.017 49.783 -94.367 49.95 60.133 52.033 48.833 51.167 37.35 47.003 12.456 47.3 107.483 36.551 31.98 39.297 -94.731 37.2 102.87 45.8 -108.533 66.533 24.65 47.733 88.083 44.12 21.95 50.017 15.733 48.768 18.593 60.433 77.867 45.5 -73.567 36.2 29.65 50.201 -104.711 50.217 -121.583 66.918 -151.518 35.833 127.117 45.283 25.033 41.1 20.817 51.317 119.617 53.133 -1.983 53.083 132.933 70.761 -117.8 37.102 36.254 60.026 -112.783 39.725 -86.282 43.356 -1.791 51.658 5.707 27.3 105.233 62.317 27.9 45.963 6.889 60.117 20.3 60.717 33.55 40.65 -86.15 73.336 139.867 49.75 -77.8 64.9 45.767 61.017 93.433 63.283 118.333 61.333 100.483 45.241 13.945 58.733 27.833 50.833 72.183 44.712 -66.801 49.467 -120.5 46.7 100.133 54.7 -7.583 33.517 126.533 30.05 101.967 60.467 23.65 44.583 4.733 45.967 23.533 50.567 3.1 55.017 -1.867 44.033 20.933 63.65 62.1 54.367 66.967 50.123 14.538 53.617 109.633 45.471 -73.741 54.817 46.583 63.45 120.317 61.531 9.402 51.833 41.483 37.855 30.368 59.583 7.383 47.017 -65.467 40.35 45.133 40.794 -73.102 41.312 -95.902 61.883 26.1 48.033 -4.733 36.22 127.99 44.722 26.657 44.317 23.867 44.8 20.467 65.867 44.217 37.483 130.9 73.0 119.867 68.883 170.783 53.017 31.6 54.017 54.15 46.1 14.367 45.883 17.2 43.677 -79.631 50.533 137.033 61.867 135.5 42.017 11.817 36.683 15.133 42.567 0.55 43.95 8.183 28.95 -107.817 35.3 75.683 46.7 -1.383 51.73 126.63 49.25 119.7 49.167 15.433 37.966 124.63 53.217 29.127 61.833 56.867 40.0 -82.883 54.367 41.933 47.667 136.

In [0]:
# Query the dataset for the first 14 days of 2025
filtered_df = spark.sql("""
    SELECT 
        latitude_dec, 
        longitude_dec, 
        snow_depth, 
        observation_date
    FROM 
        df_delta
    WHERE 
        observation_date BETWEEN '20250101' AND '20250114'
        AND snow_depth <> 9999
""")

# Convert to Pandas DataFrame for visualization
pandas_df = filtered_df.toPandas()

# Ensure snow_depth and observation_date are correctly formatted
pandas_df['snow_depth'] = pandas_df['snow_depth'].astype(float)
pandas_df['observation_date'] = pandas_df['observation_date'].astype(str)

# Ensure latitude and longitude are float values
pandas_df['latitude_dec'] = pandas_df['latitude_dec'].astype(float)
pandas_df['longitude_dec'] = pandas_df['longitude_dec'].astype(float)



In [0]:
filtered_df.createOrReplaceTempView("filtered_df_temp")


In [0]:
%sql
select distinct * from filtered_df_temp

latitude_dec longitude_dec snow_depth observation_date 69.75 27.0 0036 20250107 67.75 29.617 0049 20250106 67.367 26.633 0034 20250105 64.667 28.05 0035 20250111 67.65 24.9 0045 20250110 67.167 29.183 0045 20250109 61.833 22.467 0023 20250107 64.05 24.717 0024 20250106 61.2 26.05 0020 20250110 60.467 23.65 0010 20250106 55.35 21.467 0004 20250109 60.333 24.95 0027 20250112 60.183 24.95 0010 20250107 60.2 24.967 0022 20250112 48.717 2.383 3407 20250101 48.717 2.383 8807 20250108 45.963 6.889 0115 20250105 45.733 5.083 2207 20250104 69.133 27.267 0037 20250107 62.183 22.8 0017 20250101 64.5 26.44 0014 20250104 57.717 -4.883 0007 20250103 47.268 5.088 0000 20250103 47.783 6.367 0001 20250102 46.983 25.95 0072 20250108 46.371 25.773 0000 20250110 46.265 21.663 0000 20250101 47.344 22.094 0000 20250109 58.417 33.9 0006 20250111 57.75 22.6 0002 20250110 57.183 22.55 0004 20250105 57.35 23.117 0012 20250103 35.17 126.89 0000 20250107 45.183 22.05 0073 20250105 45.417 23.967 0007 20250105 45.039 21.71 0000 20250111 45.604 24.615 0052 20250103 48.683 116.817 0003 20250109 47.233 131.983 0013 20250101 54.417 34.017 0005 20250102 53.833 28.983 0004 20250104 49.933 15.383 7611 20250105 43.033 84.15 0020 20250110 41.733 85.817 0003 20250104 61.083 42.067 0029 20250110 60.717 33.55 0014 20250105 60.017 37.75 0021 20250109 43.117 -77.675 0010 20250108 43.117 -77.667 0005 20250111 40.65 -86.15 0005 20250112 66.333 36.017 0011 20250106 53.75 62.033 0011 20250102 58.383 97.45 0017 20250104 65.433 52.267 0033 20250102 65.433 52.267 0039 20250108 63.983 82.083 0069 20250104 48.333 -71.0 0048 20250107 48.93 -54.57 0001 20250107 49.75 -77.8 0056 20250111 66.15 -65.717 0058 20250108 49.733 -84.15 0020 20250110 62.917 152.417 0059 20250102 62.517 155.8 0038 20250107 66.367 29.317 0028 20250106 66.533 24.65 0028 20250106 66.717 27.167 0031 20250109 67.283 28.183 0040 20250105 60.6 24.8 0017 20250107 60.6 24.8 0021 20250109 60.7 26.817 0003 20250101 66.833 28.667 0027 20250108 69.583 28.9 0052 20250111 64.05 24.717 0030 20250107 56.15 21.167 0001 20250112 55.95 25.583 0007 20250104 55.617 31.183 0003 20250110 55.302 21.007 0001 20250110 54.884 23.836 0001 20250109 63.1 21.639 0012 20250101 61.05 28.15 0032 20250110 60.817 23.5 0005 20250103 60.183 24.783 0014 20250108 63.083 25.867 0026 20250104 62.6 29.717 0017 20250107 61.833 22.467 0012 20250103 61.517 28.183 0013 20250108 63.733 25.7 0026 20250104 57.083 -2.833 0002 20250104 49.017 2.533 3807 20250111 46.983 25.95 0071 20250104 46.69 22.623 0001 20250112 46.367 24.233 0002 20250111 57.317 25.333 0005 20250106 56.65 25.133 0005 20250112 56.85 26.233 0001 20250101 35.167 126.9 0002 20250109 44.088 27.966 0000 20250106 55.283 -2.283 0003 20250105 43.833 20.033 0005 20250111 43.333 21.9 0001 20250105 49.65 16.95 0001 20250110 46.867 11.033 0094 20250111 42.941 -78.736 0003 20250111 69.4 30.233 0048 20250110 68.65 43.3 0037 20250108 37.27 126.98 0000 20250106 59.5 90.928 0045 20250108 58.317 82.95 0035 20250107 53.583 92.883 0022 20250106 64.267 57.617 0061 20250110 69.933 31.983 0034 20250108 49.833 -124.483 0001 20250107 66.35 -179.117 0041 20250101 49.833 -64.283 0014 20250109 44.217 -76.6 0001 20250112 64.783 177.567 0015 20250107 58.833 151.35 0015 20250110 63.383 28.667 0031 20250104 64.3 30.167 0028 20250107 60.383 22.55 0008 20250108 69.583 28.9 0054 20250101 65.017 24.733 0017 20250108 61.85 24.283 0025 20250110 60.467 23.65 0014 20250109 56.15 21.167 0006 20250107 56.2 24.767 0001 20250106 55.955 25.591 0000 20250105 54.884 23.836 0003 20250107 62.9 27.633 0019 20250105 61.05 28.15 0042 20250111 60.183 24.95 0007 20250103 60.183 24.95 0008 20250107 60.167 22.75 0005 20250105 63.133 23.05 0017 20250102 63.083 25.867 0028 20250111 61.483 21.783 0008 20250110 62.517 24.8 0027 20250107 62.6 29.717 0013 20250102 45.733 5.083 2807 20250101 60.25 24.05 0012 20250109 61.517 28.183 0028 20250111 57.083 -2.833 0004 20250112 46.934 26.389 0000 20250102 46.318 23.139 0018 20250105 58.267 32.533 0009 20250

In [0]:
%pip install plotly


Python interpreter will be restarted.
Python interpreter will be restarted.


In [0]:
import plotly.express as px

# Create the map with Plotly
fig = px.scatter_geo(
    pandas_df,  # Data source
    lat="latitude_dec",  # Latitude column
    lon="longitude_dec",  # Longitude column
    title="Geographic Distribution of Points",  # Title of the map
    projection="natural earth"  # Map projection
)

# Display the map
fig.show()


In [0]:
# Calculate dynamic center based on mean latitude and longitude
center_lat = pandas_df['latitude_dec'].mean()
center_lon = pandas_df['longitude_dec'].mean()

print(f"Center Latitude: {center_lat}, Center Longitude: {center_lon}")


Center Latitude: 55.59815540885097, Center Longitude: 18.750928594070867


In [0]:
import plotly.express as px

# Create the animated density map
fig = px.density_mapbox(
    pandas_df,
    lat="latitude_dec",
    lon="longitude_dec",
    z="snow_depth",
    radius=10,  # Adjust radius for smoother heatmaps
    animation_frame="observation_date",  # Timeline animation based on date
    center={"lat": center_lat, "lon": center_lon},  # Dynamic centering
    zoom=2,  # Global view
    mapbox_style="carto-positron",
    title="Snow Depth Timeline - First 14 Days of 2025"
)

# Show the interactive map
fig.show()
